#### Install required packages

In [2]:
if (!require(edgeR)) {install.packages("BiocManager");BiocManager::install("edgeR")}
require(edgeR)
require(gplots)
require(feather)

Loading required package: edgeR
Warning message in library(package, lib.loc = lib.loc, character.only = TRUE, logical.return = TRUE, :
"there is no package called 'edgeR'"

package 'BiocManager' successfully unpacked and MD5 sums checked

The downloaded binary packages are in
	C:\Users\turnerevansd\AppData\Local\Temp\RtmpM96rAB\downloaded_packages


Bioconductor version 3.10 (BiocManager 1.30.10), R 3.6.1 (2019-07-05)
Installing package(s) 'BiocVersion', 'edgeR'
also installing the dependencies 'lattice', 'limma', 'locfit'



package 'lattice' successfully unpacked and MD5 sums checked
package 'limma' successfully unpacked and MD5 sums checked
package 'locfit' successfully unpacked and MD5 sums checked
package 'BiocVersion' successfully unpacked and MD5 sums checked
package 'edgeR' successfully unpacked and MD5 sums checked

The downloaded binary packages are in
	C:\Users\turnerevansd\AppData\Local\Temp\RtmpM96rAB\downloaded_packages


Old packages: 'digest', 'evaluate', 'htmltools', 'IRkernel', 'jsonlite',
  'Rcpp', 'repr', 'uuid'
Loading required package: edgeR
Warning message:
"package 'edgeR' was built under R version 3.6.2"Loading required package: limma
Warning message:
"package 'limma' was built under R version 3.6.2"Loading required package: gplots
Warning message in library(package, lib.loc = lib.loc, character.only = TRUE, logical.return = TRUE, :
"there is no package called 'gplots'"Loading required package: feather
Warning message in library(package, lib.loc = lib.loc, character.only = TRUE, logical.return = TRUE, :
"there is no package called 'feather'"

#### Load data from csv file (genes in rows, samples in columns)

In [3]:
dat=read.csv("bulkSeq.csv",as.is=T,header=T,row.names=1)
dat[1:5,1:5] #view first five rows+columns of data matrix to check that the input is correct
celltyp=(do.call(rbind,strsplit(colnames(dat),"_"))[,1])
print(unique(celltyp))
dge_table=list()

D71_r1 D71_r2  D72_r1 D72_r2 EPG1_r1
ERCC-00002 983.06 1898.90 213.52 134.27 1546.35
ERCC-00003  98.03  218.55  40.07  50.38   66.83
ERCC-00004 491.27  906.44  90.27  83.74  598.99
ERCC-00009  29.78   64.20   3.22   4.21   90.67
ERCC-00012   0.00    0.00   0.00   0.00    0.00

[1] "D71"   "D72"   "EPG1"  "EPG2"  "PEG"   "PEN2"  "whole"


#### Run differential expression among all pairs of cell types

In [4]:
celltype1_columns=which(celltyp=="D71" | celltyp=="D72")
celltype2_columns=which(celltyp=="whole")

classvec=as.factor(rep(c(1,2),times=c(length(celltype1_columns),length(celltype2_columns))))
startmat_cpm=sweep(dat[,c(celltype1_columns,celltype2_columns)],2,colSums(dat[,c(celltype1_columns,celltype2_columns)]),"/")*10^6
e_design=model.matrix(~classvec)
y2 = DGEList(counts=dat[,c(celltype1_columns,celltype2_columns)])
y2 = estimateDisp(y2, e_design)
fit = glmQLFit(y2, e_design)
qlf.2vs1 <- glmQLFTest(fit, coef=2)
outval2=topTags(qlf.2vs1,n=nrow(startmat_cpm),p.value=1)
outval2$table=outval2$table[intersect(rownames(outval2$table),rownames(startmat_cpm)),]
mean1=apply(startmat_cpm[rownames(outval2$table),classvec==1],1,mean)
mean2=apply(startmat_cpm[rownames(outval2$table),classvec==2],1,mean)
frac1=rowSums(startmat_cpm[rownames(outval2$table),classvec==1]>0)/length(celltype1_columns)
frac2=rowSums(startmat_cpm[rownames(outval2$table),classvec==2]>0)/length(celltype2_columns)
dge_table[["D7_whole"]]=cbind(outval2$table,mean1,mean2,frac1,frac2)

In [5]:
estimateDisp(DGEList(counts=dat[,c(celltype1_columns,celltype2_columns)]), e_design)

An object of class "DGEList"
$counts
           D71_r1  D71_r2 D72_r1 D72_r2 whole_brain1 whole_brain2
ERCC-00002 983.06 1898.90 213.52 134.27         2.63         3.07
ERCC-00003  98.03  218.55  40.07  50.38         0.91         0.56
ERCC-00004 491.27  906.44  90.27  83.74         4.19         6.06
ERCC-00009  29.78   64.20   3.22   4.21         0.68         0.12
ERCC-00012   0.00    0.00   0.00   0.00         0.00         0.00
17568 more rows ...

$samples
             group lib.size norm.factors
D71_r1           1 428917.7            1
D71_r2           1 418355.0            1
D72_r1           1 446320.7            1
D72_r2           1 421644.5            1
whole_brain1     1 400707.2            1
whole_brain2     1 400162.4            1

$design
  (Intercept) classvec2
1           1         0
2           1         0
3           1         0
4           1         0
5           1         1
6           1         1
attr(,"assign")
[1] 0 1
attr(,"contrasts")
attr(,"contrasts")$classvec
[1] "contr.treatment"


$common.dispersion
[1] 0.409739

$trended.dispersion
[1] 0.1657847 0.2031920 0.1735986 0.3320788 0.5173378
17568 more elements ...

$tagwise.dispersion
[1] 0.6440474 0.3907849 0.6164058 0.9328379 0.5173378
17568 more elements ...

$AveLogCPM
[1] 10.320220  7.370502  9.294403  5.496732  2.253755
17568 more elements ...

$trend.method
[1] "locfit"

$prior.df
[1] 3.007669

$prior.n
[1] 0.7519173

$span
[1] 0.3089583

In [6]:
celltype1_columns=which(celltyp=="EPG1" | celltyp=="EPG2")
celltype2_columns=which(celltyp=="whole")

classvec=as.factor(rep(c(1,2),times=c(length(celltype1_columns),length(celltype2_columns))))
startmat_cpm=sweep(dat[,c(celltype1_columns,celltype2_columns)],2,colSums(dat[,c(celltype1_columns,celltype2_columns)]),"/")*10^6
e_design=model.matrix(~classvec)
y2 = DGEList(counts=dat[,c(celltype1_columns,celltype2_columns)])
y2 = estimateDisp(y2, e_design)
fit = glmQLFit(y2, e_design)
qlf.2vs1 <- glmQLFTest(fit, coef=2)
outval2=topTags(qlf.2vs1,n=nrow(startmat_cpm),p.value=1)
outval2$table=outval2$table[intersect(rownames(outval2$table),rownames(startmat_cpm)),]
mean1=apply(startmat_cpm[rownames(outval2$table),classvec==1],1,mean)
mean2=apply(startmat_cpm[rownames(outval2$table),classvec==2],1,mean)
frac1=rowSums(startmat_cpm[rownames(outval2$table),classvec==1]>0)/length(celltype1_columns)
frac2=rowSums(startmat_cpm[rownames(outval2$table),classvec==2]>0)/length(celltype2_columns)
dge_table[["EPG_whole"]]=cbind(outval2$table,mean1,mean2,frac1,frac2)

In [7]:
celltype1_columns=which(celltyp=="PEG")
celltype2_columns=which(celltyp=="whole")

classvec=as.factor(rep(c(1,2),times=c(length(celltype1_columns),length(celltype2_columns))))
startmat_cpm=sweep(dat[,c(celltype1_columns,celltype2_columns)],2,colSums(dat[,c(celltype1_columns,celltype2_columns)]),"/")*10^6
e_design=model.matrix(~classvec)
y2 = DGEList(counts=dat[,c(celltype1_columns,celltype2_columns)])
y2 = estimateDisp(y2, e_design)
fit = glmQLFit(y2, e_design)
qlf.2vs1 <- glmQLFTest(fit, coef=2)
outval2=topTags(qlf.2vs1,n=nrow(startmat_cpm),p.value=1)
outval2$table=outval2$table[intersect(rownames(outval2$table),rownames(startmat_cpm)),]
mean1=apply(startmat_cpm[rownames(outval2$table),classvec==1],1,mean)
mean2=apply(startmat_cpm[rownames(outval2$table),classvec==2],1,mean)
frac1=rowSums(startmat_cpm[rownames(outval2$table),classvec==1]>0)/length(celltype1_columns)
frac2=rowSums(startmat_cpm[rownames(outval2$table),classvec==2]>0)/length(celltype2_columns)
dge_table[["PEG_whole"]]=cbind(outval2$table,mean1,mean2,frac1,frac2)

In [8]:
celltype1_columns=which(celltyp=="PEN2")
celltype2_columns=which(celltyp=="whole")

classvec=as.factor(rep(c(1,2),times=c(length(celltype1_columns),length(celltype2_columns))))
startmat_cpm=sweep(dat[,c(celltype1_columns,celltype2_columns)],2,colSums(dat[,c(celltype1_columns,celltype2_columns)]),"/")*10^6
e_design=model.matrix(~classvec)
y2 = DGEList(counts=dat[,c(celltype1_columns,celltype2_columns)])
y2 = estimateDisp(y2, e_design)
fit = glmQLFit(y2, e_design)
qlf.2vs1 <- glmQLFTest(fit, coef=2)
outval2=topTags(qlf.2vs1,n=nrow(startmat_cpm),p.value=1)
outval2$table=outval2$table[intersect(rownames(outval2$table),rownames(startmat_cpm)),]
mean1=apply(startmat_cpm[rownames(outval2$table),classvec==1],1,mean)
mean2=apply(startmat_cpm[rownames(outval2$table),classvec==2],1,mean)
frac1=rowSums(startmat_cpm[rownames(outval2$table),classvec==1]>0)/length(celltype1_columns)
frac2=rowSums(startmat_cpm[rownames(outval2$table),classvec==2]>0)/length(celltype2_columns)
dge_table[["PEN2_whole"]]=cbind(outval2$table,mean1,mean2,frac1,frac2)

In [9]:
celltype1_columns=which(celltyp=="D71" | celltyp=="D72")
celltype2_columns=which(celltyp=="EPG1" | celltyp=="EPG2")

classvec=as.factor(rep(c(1,2),times=c(length(celltype1_columns),length(celltype2_columns))))
startmat_cpm=sweep(dat[,c(celltype1_columns,celltype2_columns)],2,colSums(dat[,c(celltype1_columns,celltype2_columns)]),"/")*10^6
e_design=model.matrix(~classvec)
y2 = DGEList(counts=dat[,c(celltype1_columns,celltype2_columns)])
y2 = estimateDisp(y2, e_design)
fit = glmQLFit(y2, e_design)
qlf.2vs1 <- glmQLFTest(fit, coef=2)
outval2=topTags(qlf.2vs1,n=nrow(startmat_cpm),p.value=1)
outval2$table=outval2$table[intersect(rownames(outval2$table),rownames(startmat_cpm)),]
mean1=apply(startmat_cpm[rownames(outval2$table),classvec==1],1,mean)
mean2=apply(startmat_cpm[rownames(outval2$table),classvec==2],1,mean)
frac1=rowSums(startmat_cpm[rownames(outval2$table),classvec==1]>0)/length(celltype1_columns)
frac2=rowSums(startmat_cpm[rownames(outval2$table),classvec==2]>0)/length(celltype2_columns)
dge_table[["D7_EPG"]]=cbind(outval2$table,mean1,mean2,frac1,frac2)

In [10]:
celltype1_columns=which(celltyp=="D71" | celltyp=="D72")
celltype2_columns=which(celltyp=="PEG")

classvec=as.factor(rep(c(1,2),times=c(length(celltype1_columns),length(celltype2_columns))))
startmat_cpm=sweep(dat[,c(celltype1_columns,celltype2_columns)],2,colSums(dat[,c(celltype1_columns,celltype2_columns)]),"/")*10^6
e_design=model.matrix(~classvec)
y2 = DGEList(counts=dat[,c(celltype1_columns,celltype2_columns)])
y2 = estimateDisp(y2, e_design)
fit = glmQLFit(y2, e_design)
qlf.2vs1 <- glmQLFTest(fit, coef=2)
outval2=topTags(qlf.2vs1,n=nrow(startmat_cpm),p.value=1)
outval2$table=outval2$table[intersect(rownames(outval2$table),rownames(startmat_cpm)),]
mean1=apply(startmat_cpm[rownames(outval2$table),classvec==1],1,mean)
mean2=apply(startmat_cpm[rownames(outval2$table),classvec==2],1,mean)
frac1=rowSums(startmat_cpm[rownames(outval2$table),classvec==1]>0)/length(celltype1_columns)
frac2=rowSums(startmat_cpm[rownames(outval2$table),classvec==2]>0)/length(celltype2_columns)
dge_table[["D7_PEG"]]=cbind(outval2$table,mean1,mean2,frac1,frac2)

In [11]:
celltype1_columns=which(celltyp=="D71" | celltyp=="D72")
celltype2_columns=which(celltyp=="PEN2")

classvec=as.factor(rep(c(1,2),times=c(length(celltype1_columns),length(celltype2_columns))))
startmat_cpm=sweep(dat[,c(celltype1_columns,celltype2_columns)],2,colSums(dat[,c(celltype1_columns,celltype2_columns)]),"/")*10^6
e_design=model.matrix(~classvec)
y2 = DGEList(counts=dat[,c(celltype1_columns,celltype2_columns)])
y2 = estimateDisp(y2, e_design)
fit = glmQLFit(y2, e_design)
qlf.2vs1 <- glmQLFTest(fit, coef=2)
outval2=topTags(qlf.2vs1,n=nrow(startmat_cpm),p.value=1)
outval2$table=outval2$table[intersect(rownames(outval2$table),rownames(startmat_cpm)),]
mean1=apply(startmat_cpm[rownames(outval2$table),classvec==1],1,mean)
mean2=apply(startmat_cpm[rownames(outval2$table),classvec==2],1,mean)
frac1=rowSums(startmat_cpm[rownames(outval2$table),classvec==1]>0)/length(celltype1_columns)
frac2=rowSums(startmat_cpm[rownames(outval2$table),classvec==2]>0)/length(celltype2_columns)
dge_table[["D7_PEN2"]]=cbind(outval2$table,mean1,mean2,frac1,frac2)

#### View top differentially expressed genes

In [12]:
head(dge_table[["D7_whole"]])
head(dge_table[["EPG_whole"]])
head(dge_table[["PEG_whole"]])
head(dge_table[["PEN2_whole"]])

head(dge_table[["D7_EPG"]])
head(dge_table[["D7_PEG"]])
head(dge_table[["D7_PEN2"]])

logFC     logCPM    F        PValue       FDR          mean1     
FBgn0033268 11.090879  7.970648 534.1565 1.139153e-08 0.0002001834 0.04150416
FBgn0035495 11.032191 10.355877 437.2592 2.527001e-08 0.0002220349 1.59435373
FBgn0026439  9.956838  6.818256 374.1493 4.691251e-08 0.0002443949 0.02931802
FBgn0034638  9.047236  7.368555 351.9112 5.980005e-08 0.0002443949 0.60558113
FBgn0001145  9.935892  8.324752 329.9473 7.716624e-08 0.0002443949 0.65169530
FBgn0037976  9.607681  6.508815 314.3600 9.342724e-08 0.0002443949 0.03426374
            mean2     frac1 frac2
FBgn0033268  738.9172 0.25  1    
FBgn0035495 3914.7666 1.00  1    
FBgn0026439  324.9138 0.50  1    
FBgn0034638  481.0004 0.75  1    
FBgn0001145  947.0513 0.50  1    
FBgn0037976  259.5335 0.50  1

logFC     logCPM    F        PValue       FDR          mean1       
FBgn0033268 11.051490  7.970343 490.4810 3.090070e-08 0.0005430179 5.377383e-02
FBgn0013686  3.456151 15.021951 336.8158 1.277199e-07 0.0011222105 7.691331e+03
FBgn0029810  9.357502  6.502899 259.0128 3.422065e-07 0.0016392800 9.828669e-02
FBgn0002940  9.536229  7.365563 245.4886 4.181632e-07 0.0016392800 3.373571e-01
FBgn0013684  3.373363 10.407287 219.9144 6.302822e-07 0.0016392800 3.282407e+02
FBgn0028490  8.377898  6.020312 207.6025 7.809448e-07 0.0016392800 2.433614e-01
            mean2      frac1 frac2
FBgn0033268   738.9172 0.25  1    
FBgn0013686 84415.9035 1.00  1    
FBgn0029810   258.4632 0.25  1    
FBgn0002940   480.6924 0.25  1    
FBgn0013684  3404.0705 1.00  1    
FBgn0028490   180.7811 1.00  1

logFC    logCPM   F        PValue       FDR       mean1     
FBgn0011581 9.875844 7.585118 164.8672 3.872817e-05 0.1108677 0.14022628
FBgn0032840 8.778486 7.040228 158.9585 4.247743e-05 0.1108677 0.31150109
FBgn0031424 7.009669 8.129234 151.9421 4.761480e-05 0.1108677 4.05282865
FBgn0004516 7.303101 7.916275 144.3074 5.423609e-05 0.1108677 2.62597712
FBgn0250839 9.290994 6.650460 141.4997 5.699237e-05 0.1108677 0.02668558
FBgn0260964 7.840679 7.108469 124.1835 7.916010e-05 0.1108677 0.81957555
            mean2    frac1 frac2
FBgn0011581 376.6300 0.5   1    
FBgn0032840 255.6048 1.0   1    
FBgn0031424 548.6691 1.0   1    
FBgn0004516 473.2344 1.0   1    
FBgn0250839 193.5283 0.5   1    
FBgn0260964 267.8433 1.0   1

logFC     logCPM    F        PValue       FDR        mean1       
FBgn0267498 -1.447839 18.359240 793.4920 3.999173e-06 0.02787518 4.921280e+05
FBgn0001145  8.641545  8.904496 657.9700 6.017320e-06 0.02787518 2.067325e+00
FBgn0013686  4.136641 15.445133 619.3633 6.865178e-06 0.02787518 4.798946e+03
FBgn0001090 10.495545  8.498244 574.3504 8.092057e-06 0.02787518 1.898692e-01
FBgn0013675  4.147723 10.826622 527.7829 9.728355e-06 0.02787518 1.932102e+02
ERCC-00130  -6.035658 10.264777 487.8946 1.154334e-05 0.02787518 2.413902e+03
            mean2        frac1 frac2
FBgn0267498 180399.19828 1     1    
FBgn0001145    947.05133 1     1    
FBgn0013686  84415.90351 1     1    
FBgn0001090    713.71284 1     1    
FBgn0013675   3429.67293 1     1    
ERCC-00130      36.49639 1     1

logFC     logCPM   F        PValue       FDR          mean1      
FBgn0052105 -9.362551 7.006133 210.9596 4.263087e-11 7.491523e-07 247.7547161
FBgn0266872  8.666597 7.315751 148.4070 6.821971e-10 3.301425e-06   0.4537096
FBgn0034808  8.829739 8.305870 147.2567 7.246480e-10 3.301425e-06   1.0787246
FBgn0034638  8.065064 6.972161 146.5679 7.514766e-10 3.301425e-06   0.6055811
FBgn0033358  5.973404 7.768582 109.7653 6.828142e-09 2.351425e-05   6.4527890
FBgn0038532 -5.027834 6.865518 107.4182 8.028540e-09 2.351425e-05 217.5355195
            mean2        frac1 frac2
FBgn0052105   0.08560339 1.00  0.75 
FBgn0266872 308.91503845 0.25  1.00 
FBgn0034808 622.58913954 0.75  1.00 
FBgn0034638 241.23878382 0.75  1.00 
FBgn0033358 420.37026782 1.00  1.00 
FBgn0038532   6.39740786 1.00  1.00

logFC     logCPM   F         PValue       FDR          mean1    
FBgn0001145 11.440806 9.783494 173.55187 1.381753e-39 2.428155e-35 0.6516953
FBgn0034638  8.678147 6.981552 106.74632 5.272641e-25 4.632806e-21 0.6055811
FBgn0015766  8.377881 6.921585 102.43850 4.622079e-24 2.707460e-20 0.7692516
FBgn0004595  6.209985 7.530820  89.17849 3.713246e-21 1.631322e-17 6.8353627
FBgn0028490  7.016434 6.892556  87.80886 7.414389e-21 2.605861e-17 2.2919528
FBgn0033358  6.100809 7.338105  83.70442 5.894020e-20 1.726260e-16 6.4527890
            mean2     frac1 frac2
FBgn0001145 2627.6374 0.50  1    
FBgn0034638  363.1133 0.75  1    
FBgn0015766  347.3226 0.75  1    
FBgn0004595  526.3960 1.00  1    
FBgn0028490  336.9705 1.00  1    
FBgn0033358  458.8487 1.00  1

logFC      logCPM   F         PValue       FDR          mean1     
FBgn0035495   8.839225 8.183023 115.32460 3.998847e-14 6.569747e-10   1.594354
FBgn0261549   7.625286 7.149809 110.67322 7.882847e-14 6.569747e-10   1.773640
FBgn0004595   6.170085 7.495584 108.31031 1.121564e-13 6.569747e-10   6.835363
FBgn0045038 -10.091278 8.028401 100.92004 3.504151e-13 1.539461e-09 384.558333
FBgn0012344   7.330293 6.922724  89.27549 2.386607e-12 8.387970e-09   1.894184
FBgn0052105  -9.666472 7.408368  80.54543 1.126376e-11 3.298967e-08 247.754716
            mean2        frac1 frac2
FBgn0035495 854.77207459 1.0   1.0  
FBgn0261549 408.48069669 1.0   1.0  
FBgn0004595 513.75612992 1.0   1.0  
FBgn0045038   0.05935172 1.0   1.0  
FBgn0012344 346.20486230 0.5   1.0  
FBgn0052105   0.01181407 1.0   0.5

#### Save differential gene expression tables as csvs

In [13]:
for (tablename in names(dge_table)) {
    write.csv(dge_table[[tablename]],file=paste0("dge\\dge_table_",tablename,".csv"))
}